1.  Installing pyspark on google colab environment

In [1]:
# Install PySpark and Spark NLP (must use google colab)
! pip install -q pyspark==3.1.2 spark-nlp

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.4/212.4 MB 5.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 471.7/471.7 KB 18.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 198.6/198.6 KB 15.2 MB/s eta 0:00:00


2. importing google drive since we want to import the data file

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


3. importing all necessary library 

In [3]:
import pandas as pd
import numpy as np
import json
from pyspark.ml import Pipeline #import pipeline for sentiment analysis
from pyspark.sql import SparkSession #import spark session 
import pyspark.sql.functions as F
from sparknlp.annotator import * #import annotator from spark library
from sparknlp.base import *
import sparknlp
from sparknlp.pretrained import PretrainedPipeline
path='/content/drive/MyDrive/Colab Notebooks/vader_entropy.csv' #set path for the dataset in googledrive
my_data = pd.read_csv(path) #read the path set 
pd.set_option('display.max_colwidth', None)
pd.set_option('max_rows', None)

my_data

Unnamed: 0  No.                 Date                            Media  \
0              0    1  2022-11-17 00:00:00                    Theborneopost   
1              1    2  2022-11-02 00:00:00                  Theedgemalaysia   
2              2    3  2022-11-02 00:00:00                  Newsmalaysiamsn   
3              3    4  2022-11-02 00:00:00                  The Rakyat Post   
4              4    5  2022-10-24 00:00:00            The Malaysian Insight   
5              5    6  2022-10-24 00:00:00                      Thesundaily   
6              6    7  2022-10-19 00:00:00                 Selangor Journal   
7              7    8  2022-10-19 00:00:00                  Amiruddin Shari   
8              8    9  2022-10-18 00:00:00                   Business Today   
9              9   10  2022-10-14 00:00:00                 Selangor Journal   
10            10   11  2022-10-14 00:00:00                  Theedgemalaysia   
11            11   12  2022-10-13 00:00:00                 New Strait Times   
12            12   13  2022-10-04 00:00:00                  Theedgemalaysia   
13            13   14  2022-10-04 00:00:00                   Business Today   
14            14   15  2022-10-04 00:00:00                  Newsmalaysiamsn   
15            15   16  2022-09-30 00:00:00            The Malay Mail Online   
16            16   17  2022-09-28 00:00:00                 Selangor Journal   
17            17   18  2022-09-28 00:00:00                   Business Today   
18            18   19  2022-09-22 00:00:00                       i3investor   
19            19   20  2022-09-19 00:00:00                          Bernama   
20            20   21  2022-09-19 00:00:00                      Thesundaily   
21            21   22  2022-09-17 00:00:00                       i3investor   
22            22   23  2022-09-16 00:00:00                   Focus Malaysia   
23            23   24  2022-09-12 00:00:00                            Kosmo   
24            24   25  2022-09-12 00:00:00                           Utusan   
25            25   26  2022-09-08 00:00:00                         The Star   
26            26   27  2022-08-29 00:00:00                         The Star   
27            27   28  2022-08-18 00:00:00                  Theedgemalaysia   
28            28   29  2022-08-18 00:00:00                          Bernama   
29            29   30  2022-08-18 00:00:00                    Sarawak Voice   
30            30   31  2022-08-14 00:00:00                    Theborneopost   
31            31   32  2022-08-13 00:00:00              New Sarawak Tribune   
32            32   33  2022-08-13 00:00:00                          Bernama   
33            33   34  2022-08-12 00:00:00                         The Star   
34            34   35  2022-08-12 00:00:00                 Selangor Journal   
35            35   36  2022-08-12 00:00:00                         The Star   
36            36   37  2022-08-12 00:00:00                          Bernama   
37            37   38  2022-08-12 00:00:00                       i3investor   
38            38   39  2022-08-05 00:00:00                    Theborneopost   
39            39   40  2022-08-05 00:00:00                  Theedgemalaysia   
40            40   41  2022-07-27 00:00:00                          Bernama   
41            41   42  2022-07-26 00:00:00                   Business Today   
42            42   43  2022-07-26 00:00:00                          Bernama   
43            43   44  2022-07-26 00:00:00                       i3investor   
44            44   45  2022-07-25 00:00:00                  Theedgemalaysia   
45            45   46  2022-07-25 00:00:00                   Business Today   
46            46   47  2022-07-25 00:00:00            The Malay Mail Online   
47            47   48  2022-07-25 00:00:00                         The Star   
48            48   49  2022-07-25 00:00:00                          Bernama   
49            49   50  2022-07-25 00:00:00            Th

4. Convert the dataframe intro list for better sentiment process

In [4]:
text_list=[]#create the empty list
for i in my_data.index: #looping every row of data 
  text=my_data.loc[i,'News_title'] #assigning the row of data into variable text
  
  text_list.append(text) #append the text into list

text_list

['MSMEs call for moratorium to restart business',
 'Rethinking tourism with travel tech | The Edge Markets',
 'Why Are We Spending So Much Right Now',
 'Why Are We Spending So Much Right Now',
 'Issue of film industry royalty to be reviewed, says PM',
 'Issue of film practitioner royalty should be reviewed: PM',
 "OPINION | Hilman's Blurry Understanding of Economics",
 'Selangor Journal: Selangor records over RM2.1 bln in revenue from Jan to Oct, surpassing target - MB',
 'Selangor Surpasses Revenue Targets For 3rd Time Reaching RM2.1 Billion From Jan To Oct',
 'Selangor surpasses revenue target, records RM2. 065 bln',
 'ICT contributed 23.2% of GDP in 2021, DOSM reveals | The Edge Markets',
 'NST Leader: Transport sector on budget?',
 'Malaysians use credit cards more and borrow more | The Edge Markets',
 'Digitalisation Imperatives for SMEs in Malaysia',
 'Malaysians use credit cards more and borrow more',
 "Stats Dept sees Malaysia's real GDP expanding 5.1pc in 2022",
 'Tourism indu

5. Start the spark session

In [5]:
spark = sparknlp.start()

6. Set the DL model that has been defaultly created in Spark

In [6]:
MODEL_NAME='sentimentdl_use_imdb'

7. Define the Spark NLP pipeline such as universal encoder, sentimentdl and nlp

In [7]:
documentAssembler = DocumentAssembler()\
    .setInputCol("text")\
    .setOutputCol("document")
    
use = UniversalSentenceEncoder.pretrained(name="tfhub_use", lang="en")\
 .setInputCols(["document"])\
 .setOutputCol("sentence_embeddings")


sentimentdl = SentimentDLModel.pretrained(name=MODEL_NAME, lang="en")\
    .setInputCols(["sentence_embeddings"])\
    .setOutputCol("sentiment")

nlpPipeline = Pipeline(
      stages = [
          documentAssembler,
          use,
          sentimentdl
      ])


tfhub_use download started this may take some time.
Approximate size to download 923.7 MB
[OK!]
sentimentdl_use_imdb download started this may take some time.
Approximate size to download 12 MB
[OK!]


7. Run the pipeline

In [8]:
empty_df = spark.createDataFrame([['']]).toDF("text")

pipelineModel = nlpPipeline.fit(empty_df)

df = spark.createDataFrame(pd.DataFrame({"text":text_list}))
result = pipelineModel.transform(df)


8. Visualise the result via process of selecting

In [9]:
result.select(F.explode(F.arrays_zip('sentence_embeddings.result', 'sentiment.result')).alias("cols")) \
.select(F.expr("cols['0']").alias("sentence_embeddings"),
        F.expr("cols['1']").alias("sentiment")).show(truncate=False)

+----------------------------------------------------------------------------------------------------+---------+
|sentence_embeddings                                                                                 |sentiment|
+----------------------------------------------------------------------------------------------------+---------+
|MSMEs call for moratorium to restart business                                                       |neg      |
|Rethinking tourism with travel tech | The Edge Markets                                              |pos      |
|Why Are We Spending So Much Right Now                                                               |neg      |
|Why Are We Spending So Much Right Now                                                               |neg      |
|Issue of film industry royalty to be reviewed, says PM                                              |pos      |
|Issue of film practitioner royalty should be reviewed: PM                                      

9. Converting the spark dataframe into pandas dataframe

In [10]:
new=result.toPandas()
new=new.drop(columns='sentence_embeddings')
new=new.drop(columns='document')
new

text  \
0                                                                                                                                                                                                                                                                                                                                         MSMEs call for moratorium to restart business   
1                                                                                                                                                                                                                                                                                                                                Rethinking tourism with travel tech | The Edge Markets   
2                                                                                                                                                                                                                                                                                                                                                 Why Are We Spending So Much Right Now   
3                                                                                                                                                                                                                                                                                                                                                 Why Are We Spending So Much Right Now   
4                                                                                                                                                                                                                                                                                                                                Issue of film industry royalty to be reviewed, says PM   
5                                                                                                                                                                                                                                                                                                                             Issue of film practitioner royalty should be reviewed: PM   
6                                                                                                                                                                                                                                                                                                                                  OPINION | Hilman's Blurry Understanding of Economics   
7                                                                                                                                                                                                                                                                                  Selangor Journal: Selangor records over RM2.1 bln in revenue from Jan to Oct, surpassing target - MB   
8                                                                                                                                                                                                                                                                                                Selangor Surpasses Revenue Targets For 3rd Time Reaching RM2.1 Billion From Jan To Oct   
9                                                                                                                                                                                                                                                                                                                               Selangor surpasses revenue target, records RM2. 065 bln   
10                                                                                                                                                                                                        

10. Export the dataframe into excel

In [11]:
datatoexcel=pd.ExcelWriter('spark_result.xlsx')
new.to_excel(datatoexcel)
datatoexcel.save()